## Utilização do Leaflet a partir do Folium
Apresentação de algumas das funcionalidades do pacote python FOLIUM, que possibilita a geração de mapas por meio da biblioteca Javascript Leaflet (http://leafletjs.com/).

In [29]:
import os
import folium
import sys

In [30]:
lat, long = -2.885479, -60.056642

zoom_start = 8

### Parâmetros para a geração do Mapa (folium.map)
- Localização inicial (Latitude, Logitude);
- Mapa base (Tile Layer);
- Zoom inicial.

O Folium disponibiliza por padrão os seguinte Mapas base (Tile layers):
- “OpenStreetMap”
- “Mapbox Bright” 
- “Mapbox Control Room”
- “Stamen” (Terrain, Toner, and Watercolor)
- “Cloudmade” (Must pass API key)
- “Mapbox” (Must pass API key)
- “CartoDB” (positron , dark_matter)

In [31]:
m = folium.Map(location=[lat, long], tiles="OpenStreetMap", zoom_start=zoom_start)

m.save(os.path.join('resultados', 'basemap.html'))

m

## Utilização de uma base de dados geográfica (Gazetteer)
Utilização do pacote geocoder (https://github.com/DenisCarriere/geocoder) para a identificação das coordenadas de um endereço.

In [32]:
import geocoder

In [33]:
 g = geocoder.google('Avenida Darcy Vargas, 1200 , Manaus')

In [34]:
g.json

{'accuracy': 'ROOFTOP',
 'address': 'Av. Darcy Vargas, 1200 - Parque 10 de Novembro, Manaus - AM, 69030-060, Brazil',
 'bbox': {'northeast': [-3.090583819708498, -60.0163370197085],
  'southwest': [-3.093281780291502, -60.01903498029151]},
 'confidence': 9,
 'country': 'BR',
 'county': 'Manaus',
 'housenumber': '1200',
 'lat': -3.0919328,
 'lng': -60.017686,
 'ok': True,
 'place': 'ChIJifbd96QabJIRjvbKtIYST1I',
 'postal': '69030-060',
 'quality': 'street_address',
 'raw': {'address_components': [{'long_name': '1200',
    'short_name': '1200',
    'types': ['street_number']},
   {'long_name': 'Avenida Darcy Vargas',
    'short_name': 'Av. Darcy Vargas',
    'types': ['route']},
   {'long_name': 'Parque 10 de Novembro',
    'short_name': 'Parque 10 de Novembro',
    'types': ['political', 'sublocality', 'sublocality_level_1']},
   {'long_name': 'Manaus',
    'short_name': 'Manaus',
    'types': ['administrative_area_level_2', 'political']},
   {'long_name': 'Amazonas',
    'short_name': 

In [35]:
g.json['lat'], g.json['lng']

(-3.0919328, -60.017686)

## Inclusão de um marcador (ponto) no mapa

In [36]:
folium.Marker(
    location=[g.json['lat'], g.json['lng']],
    popup='UEA/EST - Escola Superior de Tecnologia',
    icon=folium.Icon(color='green', icon='ok-sign')
).add_to(m)

In [37]:
m.save(os.path.join('resultados', 'basemap_marker.html'))
m

## Inclusão de mapas base adicionais
A partir da inclusão de um componente para controle de Layers, possibilita também que os Mapas Base possam ser alternados pelo usuário.

In [38]:
folium.TileLayer('Stamen Terrain').add_to(m)
folium.TileLayer('Stamen Toner').add_to(m)
folium.LayerControl().add_to(m)

In [39]:
m.save(os.path.join('resultados', 'basemap_marker_add_base_maps.html'))
m

## Inclusão de marcadores (pontos) provenientes de um arquivo CSV.
Leitura de um arquivo CSV, com ocorrências de espécies de animais em São Paulo, usando o pacote PANDAS, e a plotagem dos dados no mapa. (Fonte dos dados de ocorrências: Portal do ICMBio)

In [40]:
lat, long = -2.885479, -60.056642
zoom_start = 6

m2 = folium.Map(location=[lat, long], tiles="Stamen Terrain", zoom_start=zoom_start)

m2.save(os.path.join('resultados', 'basemap2.html'))

m2

In [41]:
import pandas as pd
#species occurrences in the State of Sao Paulo
occurrences = pd.read_csv('dados/occ/occurrence.csv', delimiter='\t')
MAX_RECORDS = 1000

for record in occurrences[0:MAX_RECORDS].iterrows():
    folium.Marker(location = [record[1]['decimalLatitude'],record[1]['decimalLongitude']], popup=record[1]['scientificName']).add_to(m2)



In [42]:
m2.save(os.path.join('resultados', 'basemap2_markers.html'))

m2

## Inclusão de uma camada de cluster
Para melhor visualização, os marcadores (pontos), que representam as ocorrências de espécies são agrupados em clusters, que se atualizam conforme a mudança do zoom de visualização.

In [43]:
from folium.plugins import MarkerCluster
lat, long = -2.885479, -60.056642
zoom_start = 7

m3 = folium.Map(location=[lat, long], tiles="OpenStreetMap", zoom_start=zoom_start)
marker_cluster = MarkerCluster().add_to(m3)

for record in occurrences[0:MAX_RECORDS].iterrows():
    folium.Marker(location = [record[1]['decimalLatitude'],record[1]['decimalLongitude']]).add_to(marker_cluster)

m3.save(os.path.join('resultados', 'basemap3_clusters.html'))

m3

## Adicionando camadas de serviços WMS
Criação de camadas de dados a partir do consumo de serviços WMS (Web Map Service) de um servidor externo (Servidor de Mapas do ICMBio).

In [44]:
folium.WmsTileLayer(name='&Aacute;reas Priorit&aacute;rias',
                    layers = 'areas_prioritarias',            
                    url='http://mapas.icmbio.gov.br/cgi-bin/mapserv?map=/geodados/icmbio/mapfile/mma_AreasPrioritarias.map&amp;',
                    format='image/png').add_to(m3)

folium.WmsTileLayer(name='Terras Ind&iacute;genas',
                    layers = 'ti',            
                    url='http://mapas.icmbio.gov.br/cgi-bin/mapserv?map=/geodados/icmbio/mapfile/funai_TerraIndigena.map&amp;',
                    format='image/png').add_to(m3)




folium.LayerControl().add_to(m3)

m3.save(os.path.join('resultados', 'basemap3_clusters_wms.html'))

m3


## Utilização de plugins do Leaflet por meio do FOLIUM
Utilização do plugin de Mapa de Calor (HeatMap) para a verificação das áreas com maior quantidade de ocorrências de animais.

In [45]:
from folium.plugins import HeatMap
import csv

lat, long = -2.885479, -60.056642
zoom_start = 7
MAX_RECORDS = 1000

records = []
for record in occurrences[0:MAX_RECORDS].iterrows():
    records.append([record[1]['decimalLatitude'],record[1]['decimalLongitude']])
    
m4 = folium.Map(location=[lat, long], tiles="OpenStreetMap", zoom_start=zoom_start)

HeatMap(records).add_to(m4)

m4.save(os.path.join('resultados', 'basemap4_HeatMap.html'))

m4

## Inclusão de uma camada de dados a partir de um arquivo GEOJSON
Inclusão de uma camada de dados no mapa a partir de um arquivos geojson, que representa os biomas brasileiros. (Fonte: ICMBio)

In [46]:
import json

geo_json_data = json.load(open('dados/brasil/biomas.geojson'))
lat, long = -2.885479, -60.056642
zoom_start = 5

m5 = folium.Map(location=[lat, long], tiles="OpenStreetMap", zoom_start=zoom_start)

folium.GeoJson(geo_json_data, name='Biomas', overlay=True).add_to(m5)

folium.LayerControl().add_to(m5)

m5.save(os.path.join('resultados', 'basemap5_GeoJSON.html'))

m5
